In [3]:
from time import sleep
import numpy as np
import matplotlib.pyplot as plt #py -m install mataplotlib
import pandas as pd  #py -m install pandas
import io
import inspect
import datetime
from pandasql import sqldf, load_births
import requests  #pip3 -m install requests. Make sure to link pip3 to environment variable path
import os
import sqlite3
import time
import time
import glob
import os.path
from pathlib import Path

In [4]:
dbname = 'TWStock.db'

In [5]:
db = sqlite3.connect("TWStock.db")

In [6]:
pd.set_option('display.min_rows', 100)

In [7]:
pd.set_option('display.max_rows', None)

In [8]:
def crawler(date_time):
    url = 'https://www.twse.com.tw/exchangeReport/MI_INDEX?response=csv&date='+ date_time +'&type=ALLBUT0999'
    time.sleep(3)
    page = requests.get(url)
    use_text = page.text.splitlines()
    for i,text in enumerate(use_text):
        if text == '"證券代號","證券名稱","成交股數","成交筆數","成交金額","開盤價","最高價","最低價","收盤價","漲跌(+/-)","漲跌價差","最後揭示買價","最後揭示買量","最後揭示賣價","最後揭示賣量","本益比",':
            initial_point = i
            break
    test_df = pd.read_csv(io.StringIO(''.join([text[:-1] + '\n'for text in use_text[initial_point:]])))
    test_df['證券代號'] = test_df['證券代號'].apply(lambda x:x.replace('"',''))
    test_df['證券代號'] = test_df['證券代號'].apply(lambda x: x.replace('=',''))
    return test_df

In [9]:

def trans_date(date_time):
    return ''.join(str(date_time).split('-'))[0:8]


In [10]:
def parse_date(start_date, n):
    df_dict = {}
    time.sleep(3)
    now_date = start_date
    for i in range(n):
        now_date = now_date - datetime.timedelta(days=1)
        try:
            df = crawler(trans_date(now_date))
            print('successful at'+' '+ trans_date(now_date))
            df_dict.update({trans_date(now_date):df})
            time.sleep(3)
        except:
            print('fail at' + ' ' + trans_date(now_date))
            time.sleep(3)
    return df_dict


In [11]:
%%time

result_dict = parse_date(datetime.datetime.now(),2)

successful at 20210127
successful at 20210126
Wall time: 18.9 s


In [12]:
result_dict.keys()

dict_keys(['20210127', '20210126'])

In [13]:
for key in result_dict.keys():
    result_dict[key].to_csv(str(key)+'.csv')

In [14]:
ALL_csv_file = glob.glob('*.csv')

In [15]:
%%time
for file_name in ALL_csv_file:
    pd.read_csv(file_name).iloc[:,1:].to_sql(file_name.replace('.csv',''),db,if_exists='replace')

Wall time: 92.8 ms


In [16]:
cf = ALL_csv_file

In [17]:
date_list = [file_name.replace('.csv','') for file_name in ALL_csv_file]

In [18]:
total_df = pd.DataFrame()
for date in date_list:
    df = pd.read_sql(con=db,sql='SELECT * FROM' + ' "'+ date +'"')
    df['Date'] = date
    total_df = total_df.append(df)

In [19]:
total_df

index    證券代號        證券名稱         成交股數     成交筆數            成交金額  \
0         0    0050      元大台灣50   15,080,041   20,506   2,016,627,426   
1         1    0051     元大中型100       34,672       34       1,573,234   
2         2    0052        富邦科技    2,834,445    2,477     364,148,403   
3         3    0053        元大電子       52,151       44       3,447,738   
4         4    0054      元大台商50       19,160       12         587,901   
5         5    0055    元大MSCI金融       82,345       57       1,454,612   
6         6    0056       元大高股息   11,467,465    7,198     352,849,045   
7         7    0057        富邦摩台       76,062       16       6,889,692   
8         8    0061       元大寶滬深      298,130      168       7,573,859   
9         9  006203    元大MSCI台灣        8,300       10         518,885   
10       10  006204      永豐臺灣加權       15,062       17       1,197,075   
11       11  006205        富邦上証    2,022,483      453      82,380,002   
12       12  006206      元大上證50    1,102,205      167      46,278,903   
13       13  006207        FH滬深      427,915       70      14,185,081   
14       14  006208       富邦台50    4,187,476    4,601     323,068,886   
15       15  00625K      富邦上証+R       20,000        2         189,400   
16       16  00631L    元大台灣50正2    5,601,583    2,399     589,788,977   
17       17  00632R    元大台灣50反1  217,733,018   15,247   1,407,903,154   
18       18  00633L      富邦上証正2    7,080,250    1,594     567,789,956   
19       19  00634R      富邦上証反1      392,027       70       1,458,760   
20       20  00635U     元大S&P黃金      901,586      204      22,638,666   
21       21   00636     國泰中國A50    1,122,529      493      33,008,318   
22       22  00636K   國泰中國A50+U          100        1           1,044   
23       23  00637L   元大滬深300正2   70,444,953    7,586   2,222,328,411   
24       24  00638R   元大滬深300反1      600,518      129       4,456,184   
25       25   00639      富邦深100    3,257,490      757      60,062,026   
26       26  00640L      富邦日本正2      992,018       59      25,609,366   
27       27  00641R      富邦日本反1      515,000       50       5,924,730   
28       28  00642U     元大S&P石油   11,735,488    1,643     105,309,203   
29       29   00643      群益深証中小    1,611,086      395      32,159,534   
30       30  00643K    群益深証中小+R            0        0               0   
31       31   00645        富邦日本      146,963       30       3,568,280   
32       32   00646    元大S&P500      770,272      366      25,297,625   
33       33  00647L  元大S&P500正2      129,000       39       6,745,850   
34       34  00648R  元大S&P500反1    1,398,000       90      11,441,340   
35       35  00650L      FH香港正2    3,955,000      547     127,442,880   
36       36  00651R      FH香港反1      361,000       59       2,479,630   
37       37   00652        富邦印度      370,089      222       8,978,683   
38       38  00653L      富邦印度正2    5,508,249    1,498     183,111,017   
39       39  00654R      富邦印度反1      418,000      103       4,285,410   
40       40  00655L   國泰中國A50正2    4,128,500      904     248,056,320   
41       41  00656R   國泰中國A50反1      153,000       27       1,045,420   
42       42   00657     國泰日經225        3,000        3         105,330   
43       43  00657K   國泰日經225+U          100        1           1,251   
44       44   00660      元大歐洲50       29,210       25         736,423   
45       45   00661     元大日經225        9,100        6         321,612   
46       46   00662    富邦NASDAQ      286,972      139      13,843,271   
47       47  00663L    國泰臺灣加權正2       57,000       30       5,279,250   
48       48  00664R    國泰臺灣加權反1    7,567,000      903      55,739,530   
49       49  00665L    富邦恒生國企正2      398,000      135      11,721,100   
50       50  00666R    富邦恒生國企反1       91,000        7         955,160   
51       51   00668      國泰美國道瓊       17,595       22         547,795   
52       52  00668K    國泰美國道瓊+U          100        1           1,110   
53       53  00669R    國泰美國道瓊反1    8,550,000      436      78,20

In [20]:
dbname_2 = 'TWStock_2'
db2 = sqlite3.connect(dbname_2)


In [21]:
total_dict = dict(tuple(total_df.groupby('證券代號')))
for key in total_dict.keys():
    df = total_dict[key].iloc[:,2:]
    df['Date'] = pd.to_datetime(df['Date'])
    df = df.sort_values(by=['Date'])
    df.to_sql(key,db2,if_exists='replace')

In [22]:
total_df['成交股數']=total_df['成交股數'].str.replace(',','')
total_df['成交筆數']=total_df['成交筆數'].str.replace(',','')

In [23]:
total_df['成交股數'] = total_df['成交股數'].astype('str') 
total_df['成交筆數'] = total_df['成交筆數'].astype('str') 

In [22]:
total_df

index    證券代號        證券名稱       成交股數    成交筆數            成交金額       開盤價  \
0         0    0050      元大台灣50   24714046   26235   3,413,371,452    138.20   
1         1    0051     元大中型100      73357      50       3,299,870     44.62   
2         2    0052        富邦科技    2937391    2815     395,644,367    132.75   
3         3    0053        元大電子      78166      63       5,285,440     67.20   
4         4    0054      元大台商50      27000       9         821,820     30.32   
5         5    0055    元大MSCI金融      54000      25         954,090     17.75   
6         6    0056       元大高股息   12875370    6227     391,996,588     30.25   
7         7    0057        富邦摩台      43012      10       3,962,922     92.10   
8         8    0061       元大寶滬深     250330     110       6,339,929     25.50   
9         9  006203    元大MSCI台灣      15281      22         978,217     64.50   
10       10  006204      永豐臺灣加權       3086       7         247,793     80.35   
11       11  006205        富邦上証    1127247     189      45,908,562     41.07   
12       12  006206      元大上證50     333153      68      13,886,314     42.00   
13       13  006207        FH滬深     376882      57      12,528,008     33.26   
14       14  006208       富邦台50    2675859    3252     212,636,926     79.00   
15       15  00625K      富邦上証+R      20000       2         189,400      9.47   
16       16  00631L    元大台灣50正2    6168869    1653     677,617,657    109.50   
17       17  00632R    元大台灣50反1  137422428    8703     872,705,139      6.37   
18       18  00633L      富邦上証正2    6199010    1205     489,417,349     79.30   
19       19  00634R      富邦上証反1     384000      50       1,437,370      3.72   
20       20  00635U     元大S&P黃金     556716     212      14,019,191     25.25   
21       21   00636     國泰中國A50     889545     324      25,944,123     29.35   
22       22  00636K   國泰中國A50+U        100       1           1,036     10.36   
23       23  00637L   元大滬深300正2   37786051    5318   1,171,945,855     31.22   
24       24  00638R   元大滬深300反1     675586      88       5,042,963      7.45   
25       25   00639      富邦深100    1593146     336      29,071,381     18.21   
26       26  00640L      富邦日本正2     634000      47      16,505,480     25.93   
27       27  00641R      富邦日本反1     164000      30       1,877,190     11.48   
28       28  00642U     元大S&P石油   18511811    2940     166,131,668      9.06   
29       29   00643      群益深証中小     482613     160       9,605,977     20.02   
30       30  00643K    群益深証中小+R          0       0               0        --   
31       31   00645        富邦日本     128277      18       3,121,479     24.32   
32       32   00646    元大S&P500     519607     278      17,069,416     32.94   
33       33  00647L  元大S&P500正2     168000      49       8,815,450     52.55   
34       34  00648R  元大S&P500反1     565000      68       4,613,930      8.16   
35       35  00650L      FH香港正2    2550159     453      82,681,523     33.20   
36       36  00651R      FH香港反1    2549000     112      17,421,250      6.82   
37       37   00652        富邦印度     124411     104       3,103,337     25.14   
38       38  00653L      富邦印度正2    2575201     502      90,459,775     35.21   
39       39  00654R      富邦印度反1      81000      23         805,300      9.88   
40       40  00655L   國泰中國A50正2    3266000     677     193,394,950     59.50   
41       41  00656R   國泰中國A50反1      33000       9         227,610      6.88   
42       42   00657     國泰日經225       1000       1          35,130     35.13   
43       43  00657K   國泰日經225+U        100       1           1,258     12.58   
44       44   00660      元大歐洲50       7190       4         184,627     25.75   
45       45   00661     元大日經225          0       0               0        --   
46       46   00662    富邦NASDAQ     234348     103      11,220,610     48.00   
47       47  00663L    國泰臺灣加權正2      30000      17       2,891,050     95.80   
48       48  00664R    國泰臺灣加權反1    7660000     501      55,437,640      7.25   
49    

In [24]:
td2 = total_df[['證券代號','成交股數','成交筆數','Date']]

In [25]:
td2

證券代號       成交股數    成交筆數      Date
0       0050   14258565   15890  20210125
1       0051      81750      44  20210125
2       0052    3441568    3412  20210125
3       0053      59368      56  20210125
4       0054      29388      29  20210125
5       0055     125622      45  20210125
6       0056   17721831    8536  20210125
7       0057      28000       8  20210125
8       0061     433805     205  20210125
9     006203      11525      17  20210125
10    006204       6169      12  20210125
11    006205    1602292     283  20210125
12    006206    1227070     144  20210125
13    006207     584000      81  20210125
14    006208    3028485    3091  20210125
15    00625K      20000       2  20210125
16    00631L    4881258    1710  20210125
17    00632R  150483370   10498  20210125
18    00633L   11055350    1598  20210125
19    00634R     920000     105  20210125
20    00635U     502417     179  20210125
21     00636    1466830     357  20210125
22    00636K        100       1  20210125
23    00637L   77277812    7297  20210125
24    00638R     692060     160  20210125
25     00639    1941887     543  20210125
26    00640L     260000      36  20210125
27    00641R     149000      15  20210125
28    00642U   10913514    1702  20210125
29     00643    2829154     464  20210125
30    00643K       4000       2  20210125
31     00645     223650      32  20210125
32     00646    3352015     352  20210125
33    00647L      33071      30  20210125
34    00648R     505000      53  20210125
35    00650L    1904545     308  20210125
36    00651R     369000      54  20210125
37     00652     119694      77  20210125
38    00653L    4675700     933  20210125
39    00654R     122000      22  20210125
40    00655L    4062600    1077  20210125
41    00656R     378000      28  20210125
42     00657        180       2  20210125
43    00657K        100       1  20210125
44     00660      21298      12  20210125
45     00661         43       1  20210125
46     00662     272676     134  20210125
47    00663L      15000      11  20210125
48    00664R    5093099     591  20210125
49    00665L     257000      89  20210125
50    00666R     312000      18  20210125
51     00668      39238      24  20210125
52    00668K        100       1  20210125
53    00669R    1556000     143  20210125
54    00670L     520170     131  20210125
55    00671R    3240000     221  20210125
56    00673R     158000      39  20210125
57    00674R      46000      10  20210125
58    00675L     496010     358  20210125
59    00676R   10369000     459  20210125
60    00677U  120195056    6830  20210125
61     00678     328531      26  20210125
62    00680L     211000      12  20210125
63    00681R      12000       5  20210125
64    00682U     101279      33  20210125
65    00683L     395000      98  20210125
66    00684R          0       0  20210125
67    00685L      30000      21  20210125
68    00686R     141000      20  20210125
69    00688L     105000       7  20210125
70    00689R     100000       2  20210125
71     00690     191207      47  20210125
72     00692    3743154    2361  20210125
73    00693U   17732678    1985  20210125
74     00700     178098      53  20210125
75     00701    3310125     860  20210125
76     00702       5600       7  20210125
77     00703     177200      41  20210125
78    00706L          0       0  20210125
79    00707R          0       0  20210125
80    00708L    1524050     419  20210125
81     00709     111116      11  20210125
82    00710B     369303      78  20210125
83    00711B     118448      13  20210125
84     00712    2706061     835  20210125
85     00713     156113     107  20210125
86     00714     282319      34  20210125
87    00715L   32231434    2365  20210125
88     00717     811939     163  20210125
89     00728    1120899     606  20210125
90     00730     854120     296  20210125
91     00731     273501      23  20210125
92     00732     100126       3  20210125
93     00733     243875      40  20210125
94     00735     1

In [25]:
td2['成交股數'] = pd.to_numeric(td2["成交股數"])
td2['成交筆數'] = pd.to_numeric(td2["成交筆數"])

<ipython-input-25-2f4c17fe87ce>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  td2['成交股數'] = pd.to_numeric(td2["成交股數"])
<ipython-input-25-2f4c17fe87ce>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  td2['成交筆數'] = pd.to_numeric(td2["成交筆數"])


In [26]:
df_summary.iloc[0,0]

NameError: name 'df_summary' is not defined

In [1]:
%%time
container=[]
i = 0
for label, _df in td2.groupby(['證券代號']):
    _df = pd.DataFrame(_df)
   # print('===1==================')
    #print(_df)
    #print('===2=======================')
  #  print(_df.iloc[1,2])
    #_df = list(_df)
    
    _df['test']=0
    num1 = _df.iloc[0,1]
   
    num2 = _df.iloc[1,1]
    
    #print(_df[['成交股數','成交筆數']])
    _df['test'] = float(num1) < float(num2)*3
    #print(i)
    #i=i+1
    #print(num1)
   # print(float(num1)*1.7)
    #print(num2)
    #print(float(num1)*1.7 > float(num2))
    container.append(_df)
    ch_ = pd.concat(container)
    
  #  _df.loc['subtotal'] = _df[['成交股數','成交筆數']].sum()
   # print(_df.loc['subtotal'])
    

NameError: name 'td2' is not defined

In [31]:
ch_.head(2000)

證券代號       成交股數    成交筆數      Date   test
0      0050   14258565   15890  20210125   True
0      0050   15080041   20506  20210126   True
1      0051      81750      44  20210125   True
1      0051      34672      34  20210126   True
2      0052    3441568    3412  20210125   True
2      0052    2834445    2477  20210126   True
3      0053      59368      56  20210125   True
3      0053      52151      44  20210126   True
4      0054      29388      29  20210125   True
4      0054      19160      12  20210126   True
5      0055     125622      45  20210125   True
5      0055      82345      57  20210126   True
6      0056   17721831    8536  20210125   True
6      0056   11467465    7198  20210126   True
7      0057      28000       8  20210125   True
7      0057      76062      16  20210126   True
8      0061     433805     205  20210125   True
8      0061     298130     168  20210126   True
9    006203      11525      17  20210125   True
9    006203       8300      10  20210126   True
10   006204       6169      12  20210125   True
10   006204      15062      17  20210126   True
11   006205    1602292     283  20210125   True
11   006205    2022483     453  20210126   True
12   006206    1227070     144  20210125   True
12   006206    1102205     167  20210126   True
13   006207     584000      81  20210125   True
13   006207     427915      70  20210126   True
14   006208    3028485    3091  20210125   True
14   006208    4187476    4601  20210126   True
15   00625K      20000       2  20210125   True
15   00625K      20000       2  20210126   True
16   00631L    4881258    1710  20210125   True
16   00631L    5601583    2399  20210126   True
17   00632R  150483370   10498  20210125   True
17   00632R  217733018   15247  20210126   True
18   00633L   11055350    1598  20210125   True
18   00633L    7080250    1594  20210126   True
19   00634R     920000     105  20210125   True
19   00634R     392027      70  20210126   True
20   00635U     502417     179  20210125   True
20   00635U     901586     204  20210126   True
21    00636    1466830     357  20210125   True
21    00636    1122529     493  20210126   True
22   00636K        100       1  20210125   True
22   00636K        100       1  20210126   True
23   00637L   77277812    7297  20210125   True
23   00637L   70444953    7586  20210126   True
24   00638R     692060     160  20210125   True
24   00638R     600518     129  20210126   True
25    00639    1941887     543  20210125   True
25    00639    3257490     757  20210126   True
26   00640L     260000      36  20210125   True
26   00640L     992018      59  20210126   True
27   00641R     149000      15  20210125   True
27   00641R     515000      50  20210126   True
28   00642U   10913514    1702  20210125   True
28   00642U   11735488    1643  20210126   True
29    00643    2829154     464  20210125   True
29    00643    1611086     395  20210126   True
30   00643K       4000       2  20210125  False
30   00643K          0       0  20210126  False
31    00645     223650      32  20210125   True
31    00645     146963      30  20210126   True
32    00646    3352015     352  20210125  False
32    00646     770272     366  20210126  False
33   00647L      33071      30  20210125   True
33   00647L     129000      39  20210126   True
34   00648R     505000      53  20210125   True
34   00648R    1398000      90  20210126   True
35   00650L    1904545     308  20210125   True
35   00650L    3955000     547  20210126   True
36   00651R     369000      54  20210125   True
36   00651R     361000      59  20210126   True
37    00652     119694      77  20210125   True
37    00652     370089     222  20210126   True
38   00653L    4675700     933  20210125   True
38   00653L    5508249    1498  20210126   True
39   00654R     122000      22  20210125   True
39   00654R     418000     103  20210126   True
40   00655L    4062600    1077  20210125   True
40   00655L    4128500     904  20210126   True
41   00656R     378000 

In [32]:
ch_.sort_values(by=['test'], ascending=False)

證券代號       成交股數    成交筆數      Date   test
0       0050   14258565   15890  20210125   True
745     3376     840202     658  20210126   True
742     3338     381270     318  20210126   True
743     3346    1830418    1087  20210125   True
743     3346    3238870    2050  20210126   True
744     3356     492213     348  20210125   True
744     3356     528163     322  20210126   True
745     3376     847281     598  20210125   True
746     3380    3033483    1751  20210125   True
750     3416      25510      28  20210125   True
746     3380    4016427    2262  20210126   True
747     3383      62896      20  20210125   True
747     3383     302992      60  20210126   True
748     3406    7751111    7018  20210125   True
748     3406    3907384    3839  20210126   True
749     3413    4468408    3231  20210125   True
742     3338     423303     350  20210125   True
741     3321     369016     240  20210126   True
741     3321     859878     465  20210125   True
740     3312     854984     383  20210126   True
740     3312    2207615     984  20210125   True
739     3311     119763      80  20210126   True
739     3311     132396      94  20210125   True
738     3308      20322      20  20210126   True
738     3308      26738      39  20210125   True
737     3305     898358     510  20210126   True
737     3305     862211     520  20210125   True
736     3296     901100     464  20210126   True
736     3296    1331302     576  20210125   True
735     3266      97000      46  20210126   True
735     3266      18000       9  20210125   True
734     3257     499105     414  20210126   True
734     3257     357746     285  20210125   True
749     3413    5209655    3994  20210126   True
750     3416      67226      39  20210126   True
767     3535     292517     171  20210126   True
763     3528      37281      23  20210125   True
760     3504     220000     178  20210125   True
760     3504     204505     152  20210126   True
761     3515     986967     841  20210125   True
761     3515     807369     685  20210126   True
762     3518     102608      75  20210125   True
762     3518     102203      53  20210126   True
763     3528      21005      23  20210126   True
751     3419    1453462     724  20210125   True
764     3530    2107245    1603  20210125   True
764     3530    1805703    1413  20210126   True
765     3532    1727538    1365  20210125   True
765     3532    1490614    1121  20210126   True
766     3533     605155     625  20210125   True
766     3533     446182     510  20210126   True
759     3501     189699     138  20210126   True
759     3501      97770      82  20210125   True
758     3494     353011     131  20210126   True
758     3494     441505     189  20210125   True
757     3481  122945632   19395  20210126   True
757     3481  119137767   18027  20210125   True
756     3454     203303     176  20210126   True
756     3454     330984     263  20210125   True
755     3450    1045417     818  20210126   True
755     3450    1038135     758  20210125   True
754     3443    5083930    4619  20210126   True
754     3443    6226562    5295  20210125   True
753     3437    5411951    2960  20210126   True
753     3437    4966299    2643  20210125   True
752     3432     143641      60  20210126   True
752     3432     132000      67  20210125   True
751     3419    1250005     588  20210126   True
733     3231   14395378    8015  20210126   True
733     3231   18312553    7469  20210125   True
732     3229      75004      29  20210126   True
711     3049    4030006    1200  20210125   True
708     3046     204027     166  20210125   True
708     3046     101281      72  20210126   True
709     3047    1100358     485  20210125   True
709     3047     918939     393  20210126   True
710     3048    1143200     624  20210125   True
710     3048    1497467     825  20210126   True
711     3049    2892210     943  20210126   True
732     3229      45031      30  20210125   True
712     3050    1925623     926  202101

In [ ]:
8422 6196 3593 1453 4720